# Inference and RAG with LLama Model

# Install Required Libraries

In [ ]:
%%capture
# Installs Unsloth, Xformers (Flash Attention) and all other packages!
!pip install "unsloth[colab-new] @ git+https://github.com/unslothai/unsloth.git"
!pip install --no-deps "xformers<0.0.27" "trl<0.9.0" peft accelerate bitsandbytes

# Load Data

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
import json

similar_test_path = "/content/drive/MyDrive/spider/test_similar_questions/sampled_similar_questions_v2.json"
with open(similar_test_path, 'r') as f:
    similar_data = json.load(f)

In [ ]:
similar_data[0]

{'question': 'Find the name of the sailors who reserved boat with id 103.',
 'db_id': 'boat_1',
 'similar_q': [{'db_id': 'ship_1',
   'original_question': 'Find the name of the ship that is steered by the youngest captain.',
   'sql_query': 'SELECT t1.name FROM ship AS t1 JOIN captain AS t2 ON t1.ship_id  =  t2.ship_id ORDER BY t2.age LIMIT 1'},
  {'db_id': 'ship_1',
   'original_question': 'Find the name of the ships that have more than one captain.',
   'sql_query': 'SELECT t1.name FROM ship AS t1 JOIN captain AS t2 ON t1.ship_id  =  t2.ship_id GROUP BY t2.ship_id HAVING count(*)  >  1'},
  {'db_id': 'ship_1',
   'original_question': 'Find the name of the ships that are steered by both a captain with Midshipman rank and a captain with Lieutenant rank.',
   'sql_query': "SELECT t1.name FROM ship AS t1 JOIN captain AS t2 ON t1.ship_id  =  t2.ship_id WHERE t2.rank  =  'Midshipman' INTERSECT SELECT t1.name FROM ship AS t1 JOIN captain AS t2 ON t1.ship_id  =  t2.ship_id WHERE t2.rank  =  

In [ ]:
db_test_path = "/content/drive/MyDrive/spider/db_tables_str.json"
with open(db_test_path, 'r') as f:
    db_data = json.load(f)

## Load LLama Model

In [ ]:
from unsloth import FastLanguageModel

model, tokenizer = FastLanguageModel.from_pretrained(
    model_name = "unsloth/llama-3-8b-Instruct-bnb-4bit",
    max_seq_length = 8192,
    load_in_4bit = True,
)

🦥 Unsloth: Will patch your computer to enable 2x faster free finetuning.


config.json:   0%|          | 0.00/1.15k [00:00<?, ?B/s]

==((====))==  Unsloth: Fast Llama patching release 2024.7
   \\   /|    GPU: Tesla T4. Max memory: 14.748 GB. Platform = Linux.
O^O/ \_/ \    Pytorch: 2.3.1+cu121. CUDA = 7.5. CUDA Toolkit = 12.1.
\        /    Bfloat16 = FALSE. FA [Xformers = 0.0.26.post1. FA2 = False]
 "-____-"     Free Apache license: http://github.com/unslothai/unsloth
Unsloth: Fast downloading is enabled - ignore downloading bars which are red colored!


model.safetensors:   0%|          | 0.00/5.70G [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/131 [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/51.1k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/9.09M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/459 [00:00<?, ?B/s]

In [ ]:
from transformers import TextStreamer
from unsloth.chat_templates import get_chat_template
tokenizer = get_chat_template(
    tokenizer,
    chat_template = "llama-3",
    mapping = {"role" : "from", "content" : "value", "user" : "human", "assistant" : "gpt"}, # ShareGPT style
)
FastLanguageModel.for_inference(model) # Enable native 2x faster inference

## Extract SQL from LLM output

In [ ]:
import re

def extract_sql_statements(text):
    sql_statements = re.findall(r'```sql(.*?)```', text, re.DOTALL)
    return [statement.strip() for statement in sql_statements]

## Prompting Using Both Similar Samples and Tables info

In [ ]:
alpaca_prompt = """
### Instruction:
You are a helpful assistant that produces SQL Queries from the given question.
You should output a SQL query that is syntactically correct and can be executed without error.
In the input, you will recieve the question and similar text-to-sql pairs in addition to database tables for question.
Please output in the following format so it would be easy to extract SQL query. You should put sql code between
```sql SQL ```:
```sql
SELECT count(*) FROM head WHERE age  >  56;
```


### Input:
{}

Question: {}
Database: {}
Database tables:
{}

SQL:
"""

In [ ]:
def questions_to_str(q_list):
    q_sql_format = """
        Question: {}
        Database: {}
        SQL:{}

    """
    q_all = " "
    for q in q_list:
        q_all += q_sql_format.format(q['original_question'], q['db_id'], q['sql_query'])

    return q_all

predicted_queries = []
full_results = []

for item in similar_data:
    question = item['question']
    similar_questions = item['similar_q']
    db_id = item['db_id']
    tabs = db_data[db_id]
    similar_formatted = questions_to_str(similar_questions)
    prompt = alpaca_prompt.format(simialr_formatted, question, db_id, "\n".join(tabs))

    messages = [
    {"from": "human", "value": prompt},
    ]
    inputs = tokenizer.apply_chat_template(messages, tokenize = True, add_generation_prompt = True, return_tensors = "pt").to("cuda")

    text_streamer = TextStreamer(tokenizer)
    result = model.generate(input_ids = inputs, streamer = text_streamer, max_new_tokens = 1024, use_cache = True)
    text_res = tokenizer.batch_decode(result)[0]
    full_results.append(text_res)
    pred_query = extract_sql_statements(text_res)[-1]
    predicted_queries.append(pred_query)

### Formatting generated Query

In [ ]:
revised_filtered_queries = []

for pred in predicted_queries:
    pred = pred.replace("\n", " ")
    if pred[-1] != ';':
        pred += ';'
    revised_filtered_queries.append(pred)

revised_filtered_queries

In [ ]:
with open('/content/drive/MyDrive/spider/results/sampled_tables_rag_llama.txt', mode='wt', encoding='utf-8') as myfile:
    myfile.write('\n'.join(revised_filtered_queries))

## Prompt just Tables info

In [ ]:
alpaca_prompt_v2 = """
### Instruction:
You are a helpful assistant that produces SQL Queries from the given question.
You should output a SQL query that is syntactically correct and can be executed without error.
In the input, you will recieve the question and  database tables for question.
Please output in the following format so it would be easy to extract SQL query. You should put sql code between
```sql SQL ```:
```sql
SELECT count(*) FROM head WHERE age  >  56;
```


### Input:

Question: {}
Database: {}
Database tables:
{}

SQL:
"""

In [ ]:
def questions_to_str(q_list):
    q_sql_format = """
        Question: {}
        Database: {}
        SQL:{}

    """
    q_all = " "
    for q in q_list:
        q_all += q_sql_format.format(q['original_question'], q['db_id'], q['sql_query'])

    return q_all

predicted_queries = []
full_results = []

for item in similar_data:
    question = item['question']
    db_id = item['db_id']
    tabs = db_data[db_id]
    prompt = alpaca_prompt_v2.format(question, db_id, "\n".join(tabs))

    messages = [
    {"from": "human", "value": prompt},
    ]
    inputs = tokenizer.apply_chat_template(messages, tokenize = True, add_generation_prompt = True, return_tensors = "pt").to("cuda")

    text_streamer = TextStreamer(tokenizer)
    result = model.generate(input_ids = inputs, streamer = text_streamer, max_new_tokens = 1024, use_cache = True)
    text_res = tokenizer.batch_decode(result)[0]
    full_results.append(text_res)
    pred_query = extract_sql_statements(text_res)[-1]
    predicted_queries.append(pred_query)

The attention mask is not set and cannot be inferred from input because pad token is same as eos token.As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.


Streaming output truncated to the last 5000 lines.

```sql
SELECT COUNT(*) 
FROM author a 
JOIN author_list al ON a.author_id = al.author_id 
JOIN paper p ON al.paper_id = p.paper_id 
WHERE a.name = 'Mckeown, Kathleen';
```<|eot_id|>
<|begin_of_text|><|start_header_id|>user<|end_header_id|>

### Instruction:
You are a helpful assistant that produces SQL Queries from the given question.
You should output a SQL query that is syntactically correct and can be executed without error.
In the input, you will recieve the question and  database tables for question.
Please output in the following format so it would be easy to extract SQL query. You should put sql code between
```sql SQL ```:
```sql
SELECT count(*) FROM head WHERE age  >  56;
```


### Input:

Question: What is the name and number of citations of the author with the greatest number of citations among authors?
Database: aan_1
Database tables:
affiliation(affiliation_id, name, address, )
author(author_id, name, email, )
author list

In [ ]:
predicted_queries

['SELECT s.name \nFROM sailors AS s \nJOIN reserves AS r ON s.sid = r.sid \nWHERE r.bid = 103;',
 "SELECT s.name \nFROM sailors AS s \nJOIN reserves AS r ON s.sid = r.sid \nJOIN boats AS b ON r.bid = b.bid \nWHERE b.name = 'Melon';",
 "SELECT avg(Units_sold_Millions) \nFROM game \nWHERE Platform_ID IN (\n  SELECT Platform_ID \n  FROM game \n  JOIN game_player ON game.Game_ID = game_player.Game_ID \n  JOIN player ON game_player.Player_ID = player.Player_ID \n  WHERE Position = 'Guard'\n)",
 "SELECT Collection_Name \nFROM collections \nWHERE Collection_ID IN (\n  SELECT Collection_ID \n  FROM documents_in_collections \n  WHERE Document_Object_ID IN (\n    SELECT Document_Object_ID \n    FROM document_subset_members \n    WHERE Document_Subset_ID IN (\n      SELECT Document_Subset_ID \n      FROM document_subsets \n      WHERE Document_Subset_Name LIKE '%Best%'\n    )\n  )\n);",
 'SELECT Analytical_Layer_Type_Code \nFROM analytical_layer \nGROUP BY Analytical_Layer_Type_Code \nORDER BY CO

In [ ]:
revised_filtered_queries = []

In [ ]:
for pred in predicted_queries:
    pred = pred.replace("\n", " ")
    if pred[-1] != ';':
        pred += ';'
    revised_filtered_queries.append(pred)

revised_filtered_queries

['SELECT name  FROM sailors  WHERE sid IN (   SELECT sid    FROM reserves    WHERE bid = 103 );',
 "SELECT s.name  FROM sailors s  JOIN reserves r ON s.sid = r.sid  JOIN boats b ON r.bid = b.bid  WHERE b.name = 'Melon';",
 "SELECT AVG(Units_sold_Millions)  FROM game  WHERE Platform_ID IN (   SELECT Platform_ID    FROM game    JOIN player ON game.Game_ID = game_player.Game_ID    WHERE player.Position = 'Guard' );",
 "SELECT Collection_Name  FROM collections  WHERE Collection_ID IN (   SELECT Collection_ID    FROM documents_in_collections    WHERE Document_Object_ID IN (     SELECT Document_Object_ID      FROM document_subset_members      WHERE Document_Subset_ID IN (       SELECT Document_Subset_ID        FROM document_subsets        WHERE Document_Subset_Name = 'Best'     )   ) );",
 'SELECT      Analytical_Layer_Type_Code,      COUNT(*) AS Frequency FROM      analytical_layer GROUP BY      Analytical_Layer_Type_Code ORDER BY      Frequency DESC LIMIT 1;',
 'SELECT      Nationality,   

In [ ]:
full_results

['<|begin_of_text|><|start_header_id|>user<|end_header_id|>\n\n### Instruction:\nYou are a helpful assistant that produces SQL Queries from the given question.\nYou should output a SQL query that is syntactically correct and can be executed without error.\nIn the input, you will recieve the question and  database tables for question.\nPlease output in the following format so it would be easy to extract SQL query. You should put sql code between\n```sql SQL ```:\n```sql\nSELECT count(*) FROM head WHERE age  >  56;\n```\n\n\n### Input:\n\nQuestion: Find the name of the sailors who reserved boat with id 103.\nDatabase: boat_1\nDatabase tables:\nsailors(sid, name, rating, age, )\nboats(bid, name, color, )\nreserves(sid, bid, day, )\n\nSQL:<|eot_id|><|start_header_id|>assistant<|end_header_id|>\n\n```sql\nSELECT name \nFROM sailors \nWHERE sid IN (\n  SELECT sid \n  FROM reserves \n  WHERE bid = 103\n);\n```<|eot_id|>',
 "<|begin_of_text|><|start_header_id|>user<|end_header_id|>\n\n### Inst

In [ ]:
with open('/content/drive/MyDrive/spider/results/sampled_tables_wo_samples_llama.txt', mode='wt', encoding='utf-8') as myfile:
    myfile.write('\n'.join(revised_filtered_queries))

# Prompt Just Similar Data

In [ ]:
alpaca_prompt_v3 = """
### Instruction:
You are a helpful assistant that produces SQL Queries from the given question and related samples. You should
output a SQL query that is syntactically correct and can be executed without error. In the input,
you will recive the question and similar text-to-sql pairs.
Please output in the following format so it would be easy to extract SQL query:
```sql
SELECT AVG("Working_Horses")
FROM "farm"
WHERE "Total_Horses" > 5000;
```

### Input:
{}

Question: {}
Database: {}

SQL:
"""

In [ ]:
def questions_to_str(q_list):
    q_sql_format = """
        Question: {}
        Database: {}
        SQL:{}

    """
    q_all = " "
    for q in q_list:
        q_all += q_sql_format.format(q['original_question'], q['db_id'], q['sql_query'])

    return q_all

predicted_queries = []

for text, db_id in zip(similar_data, db_names):
    similar_questions = similar_data[text]
    similar_formatted = questions_to_str(similar_questions)
    prompt = alpaca_prompt_v3.format(similar_formatted, text, db_id)

    messages = [
    {"from": "human", "value": prompt},
    ]
    inputs = tokenizer.apply_chat_template(messages, tokenize = True, add_generation_prompt = True, return_tensors = "pt").to("cuda")

    text_streamer = TextStreamer(tokenizer)
    result = model.generate(input_ids = inputs, streamer = text_streamer, max_new_tokens = 1024, use_cache = True)
    text_res = tokenizer.batch_decode(result)[0]
    pred_query = extract_sql_statements(text_res)[-1]
    predicted_queries.append(pred_query)

The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


<|begin_of_text|><|start_header_id|>user<|end_header_id|>

### Instruction:
You are a helpful assistant that produces SQL Queries from the given question and related samples. You should
output a SQL query that is syntactically correct and can be executed without error. In the input, 
you will recive the question and similar text-to-sql pairs.
Please output in the following format so it would be easy to extract SQL query:
```sql
SELECT AVG("Working_Horses")
FROM "farm"
WHERE "Total_Horses" > 5000;
```

### Input:
 
        Question: How many clubs are there?
        Database: sports_competition
        SQL:SELECT count(*) FROM club
    
    
        Question: How many clubs are there?
        Database: club_1
        SQL:SELECT count(*) FROM club
    
    
        Question: What is the total number of clubs?
        Database: sports_competition
        SQL:SELECT count(*) FROM club
    
    
        Question: How many book clubs are there?
        Database: culture_company
        SQL:S

The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


<|begin_of_text|><|start_header_id|>user<|end_header_id|>

### Instruction:
You are a helpful assistant that produces SQL Queries from the given question and related samples. You should
output a SQL query that is syntactically correct and can be executed without error. In the input, 
you will recive the question and similar text-to-sql pairs.
Please output in the following format so it would be easy to extract SQL query:
```sql
SELECT AVG("Working_Horses")
FROM "farm"
WHERE "Total_Horses" > 5000;
```

### Input:
 
        Question: Count the total number of clubs.
        Database: club_1
        SQL:SELECT count(*) FROM club
    
    
        Question: What is the total number of clubs?
        Database: sports_competition
        SQL:SELECT count(*) FROM club
    
    
        Question: Count the number of book clubs.
        Database: culture_company
        SQL:SELECT count(*) FROM book_club
    
    
        Question: How many clubs are there?
        Database: sports_competition


The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


...

<|begin_of_text|><|start_header_id|>user<|end_header_id|>

### Instruction:
You are a helpful assistant that produces SQL Queries from the given question and related samples. You should
output a SQL query that is syntactically correct and can be executed without error. In the input, 
you will recive the question and similar text-to-sql pairs.
Please output in the following format so it would be easy to extract SQL query:
```sql
SELECT AVG("Working_Horses")
FROM "farm"
WHERE "Total_Horses" > 5000;
```

### Input:
 
        Question: Find the schools that were either founded after 1850 or public.
        Database: university_basketball
        SQL:SELECT school FROM university WHERE founded  >  1850 OR affiliation  =  'Public'
    
    
        Question: Which locations contains both shops that opened after the year 2012 and shops that opened before 2008?
        Database: device
        SQL:SELECT LOCATION FROM shop WHERE Open_Year  >  2012 INTERSECT SELECT LOCATION FROM shop WHERE Open

The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


<|begin_of_text|><|start_header_id|>user<|end_header_id|>

### Instruction:
You are a helpful assistant that produces SQL Queries from the given question and related samples. You should
output a SQL query that is syntactically correct and can be executed without error. In the input, 
you will recive the question and similar text-to-sql pairs.
Please output in the following format so it would be easy to extract SQL query:
```sql
SELECT AVG("Working_Horses")
FROM "farm"
WHERE "Total_Horses" > 5000;
```

### Input:
 
        Question: What are the schools that were either founded before 1850 or are public?
        Database: university_basketball
        SQL:SELECT school FROM university WHERE founded  >  1850 OR affiliation  =  'Public'
    
    
        Question: What campuses opened between 1935 and 1939?
        Database: csu_1
        SQL:SELECT campus FROM campuses WHERE YEAR  >=  1935 AND YEAR  <=  1939
    
    
        Question: What campuses opened before 1800?
        Database: 

The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


<|begin_of_text|><|start_header_id|>user<|end_header_id|>

### Instruction:
You are a helpful assistant that produces SQL Queries from the given question and related samples. You should
output a SQL query that is syntactically correct and can be executed without error. In the input, 
you will recive the question and similar text-to-sql pairs.
Please output in the following format so it would be easy to extract SQL query:
```sql
SELECT AVG("Working_Horses")
FROM "farm"
WHERE "Total_Horses" > 5000;
```

### Input:
 
        Question: What are the maximum and average height of the mountains?
        Database: mountain_photos
        SQL:SELECT max(height),  avg(height) FROM mountain
    
    
        Question: What is the detail of the location UK Gallery?
        Database: cre_Theme_park
        SQL:SELECT Other_Details FROM LOCATIONS WHERE Location_Name  =  "UK Gallery"
    
    
        Question: How many artworks are there?
        Database: entertainment_awards
        SQL:SELECT cou

In [ ]:
revised_filtered_queries = []

for pred in predicted_queries:
    pred = pred.replace("\n", " ")
    if pred[-1] != ';':
        pred += ';'
    revised_filtered_queries.append(pred)

revised_filtered_queries

In [ ]:
with open('/content/drive/MyDrive/spider/results/sampled_samples_llama.txt', mode='wt', encoding='utf-8') as myfile:
    myfile.write('\n'.join(revised_filtered_queries))